In [1]:
import scipy
import numpy as np
import pandas as pd
import plotly.plotly as py
from plotly.graph_objs import *
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from sklearn import preprocessing, metrics
from sklearn.cross_validation import train_test_split, cross_val_score
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.grid_search import GridSearchCV, RandomizedSearchCV
from scipy.stats.distributions import randint
import locale
init_notebook_mode()

print("libraries all import")

libraries all import


In [2]:
locale.setlocale(locale.LC_NUMERIC, '')
load = pd.read_csv('data/Load_history.csv', thousands=',')

In [3]:
temperature = pd.read_csv('data/temperature_history.csv', sep=',')

In [11]:
load.head(2)

zone_id  year  month  day     h1     h2     h3     h4     h5     h6  ...    \
0        1  2004      1    1  16853  16450  16517  16873  17064  17727  ...     
1        1  2004      1    2  14155  14038  14019  14489  14920  16072  ...     

     h15    h16    h17    h18    h19    h20    h21    h22    h23    h24  
0  13518  13138  14130  16809  18150  18235  17925  16904  16162  14750  
1  16127  15448  15839  17727  18895  18650  18443  17580  16467  15258  

[2 rows x 28 columns]

In [4]:
loadhour = load[load.columns[4:]]
load['date'] = pd.to_datetime(load.year*10000 + load.month*100 + load.day, format='%Y%m%d')
load['dayagg'] = loadhour.sum(axis=1)
load.head(2)

zone_id  year  month  day     h1     h2     h3     h4     h5     h6  \
0        1  2004      1    1  16853  16450  16517  16873  17064  17727   
1        1  2004      1    2  14155  14038  14019  14489  14920  16072   

    ...      h17    h18    h19    h20    h21    h22    h23    h24       date  \
0   ...    14130  16809  18150  18235  17925  16904  16162  14750 2004-01-01   
1   ...    15839  17727  18895  18650  18443  17580  16467  15258 2004-01-02   

   dayagg  
0  400880  
1  408157  

[2 rows x 30 columns]

In [8]:
displayLoad = (load[['dayagg', 'date']]).groupby(['date']).sum()
displayLoad.shape

(1650, 1)

In [103]:
# Create a trace
data = [Scatter(
    x = pd.date_range('1/1/2004', '7/7/2008'),
    y = displayLoad.dayagg/1000000,
    #x = pd.date_range('1/1/2005', '31/12/2005'),
    #y = displayLoad.dayagg[:365]/1000000,
    mode = "lines"
)]

layout = Layout(
    title = 'Total Daily Load',
    xaxis = dict(title='Date'),
    yaxis = dict(title = "Load(Million)")
)
fig = dict(data=data, layout = layout)
iplot(fig)

In [19]:
nrow, ncol = loadhour.shape
header =  loadhour.columns.values
data = [
    Box(
        y = loadhour[loadhour.columns[i]],
        name = header[i],
        marker = dict(color = "purple"),
    ) for i in range(ncol)
]
layout = Layout(
    title = 'Hourly Load distribution aggregated by Zone',
    xaxis = dict(title = "Feature"),
    yaxis = dict(title = "Value"),
    showlegend = False
)

fig = dict(data=data, layout=layout)

iplot(fig)

In [104]:
# For Hour Group
data = [Scatter(
    x = range(1,25),
    y = loadhour.mean(),
    mode = "lines+markers"
)]

layout = Layout(
    title = 'Mean of Hourly Load',
    xaxis = dict(title='Hour'),
    yaxis = dict(title = "Load(Million)")
)
fig = dict(data=data, layout = layout)
iplot(fig)
# proposed hour group: Group0(sleep)->(23,24,1-7), Group1(working)->(8-17), Group3(leisure)->(18-22)

In [12]:
loadZone = load[['zone_id', 'dayagg']]
rows = loadZone[loadZone.zone_id==2]
rows = range(1, 1651)
index = range(1,21)
zones = []
for i in index:
    zones.append('zone'+`i`)
display2 = pd.DataFrame(index=rows, columns=zones)
display2 = display2.fillna(0)

In [13]:
for i in index:
    tmp = loadZone[loadZone.zone_id == i]
    display2[[zones[i-1]]] = tmp.dayagg.values

In [14]:
display2.head()
display3 = display2[display2 != 0]

In [16]:
nrow, ncol = display3.shape
header =  display3.columns.values
data = [
    Box(
        y = display3[display3.columns[i]],
        name = header[i],
        marker = dict(color = "purple"),
    ) for i in range(ncol)
]

layout = Layout(
    title = 'Daily Load Distribution by Zone',
    xaxis = dict(title = "Zone"),
    yaxis = dict(title = "Load"),
    showlegend = False
)

fig = dict(data=data, layout=layout)

iplot(fig)

In [53]:
temphour = temperature[temperature.columns[4:]]
temperature['date'] = pd.to_datetime(temperature.year*10000 + temperature.month*100 + temperature.day, format='%Y%m%d')
temperature['daymean'] = temphour.mean(axis=1)
temperature.head(2)

station_id  year  month  day  h1  h2  h3  h4  h5  h6    ...      h17  h18  \
0           1  2004      1    1  46  46  45  41  39  35    ...       52   46   
1           1  2004      1    2  43  44  46  46  47  47    ...       57   53   

   h19  h20  h21  h22  h23  h24       date    daymean  
0   40   40   39   38   40   41 2004-01-01  44.333333  
1   50   47   46   45   45   45 2004-01-02  48.458333  

[2 rows x 30 columns]

In [56]:
displayTemp = (temperature[['daymean', 'date']]).groupby(['date']).mean()

In [72]:
data = [Scatter(
    x = pd.date_range('1/1/2004', '30/6/2008'),
    y = displayTemp['daymean'],
    mode = "lines"
)]
layout = Layout(
    title = 'Daily Averaged Temperature',
    xaxis = dict(title= "Date"),
    yaxis = dict(title = "Temperature")
)
fig = dict(data=data, layout = layout)
iplot(fig)

In [83]:
data1 = Scatter(
    x = pd.date_range('1/1/2004', '30/6/2008'),
    y = displayTemp.daymean,
    name = 'Temperature',
    line = dict(
        color=('rgb(205,12,24)'),
        width = 1)
)

data2 = Scatter(
    x = pd.date_range('1/1/2004', '30/6/2008'),
    y = (displayLoad.dayagg[:1643])/1000000,
    name = 'Load',
    line = dict(
        color = ('rgb(22, 96, 167)'),
        width = 1)
)

layout = Layout(
    title = 'Daily Averaged Temperature',
    xaxis = dict(title= "Date"),
    yaxis = dict(title = "Load&Temperature")
)
fig = dict(data=[data1, data2], layout=layout)
iplot(fig)

In [24]:
holidays = pd.read_csv('data/add/Holidays.csv', sep=',')

In [25]:
holidays

Unnamed: 0                   2004  \
0                       New Year's Day    Thursday, January 1   
1  Birthday of Martin Luther King, Jr.     Monday, January 19   
2                Washington's Birthday    Monday, February 16   
3                         Memorial Day         Monday, May 31   
4                     Independence Day         Monday, July 5   
5                            Labor Day    Monday, September 6   
6                         Columbus Day     Monday, October 11   
7                         Veterans Day  Thursday, November 11   
8                     Thanksgiving Day  Thursday, November 25   
9                        Christmas Day    Friday, December 24   

                        2005                   2006                   2007  \
0  Friday, December 31, 2004      Monday, January 2      Monday, January 1   
1         Monday, January 17     Monday, January 16     Monday, January 15   
2        Monday, February 21    Monday, February 20    Monday, February 19   
3             Monday, May 30         Monday, May 29         Monday, May 28   
4             Monday, July 4        Tuesday, July 4      Wednesday, July 4   
5        Monday, September 5    Monday, September 4    Monday, September 3   
6         Monday, October 10      Monday, October 9      Monday, October 8   
7        Friday, November 11    Friday, November 10    Monday, November 12   
8      Thursday, November 24  Thursday, November 23  Thursday, November 22   
9        Monday, December 26    Monday, December 25   Tuesday, December 25   

                  2008  
0   Tuesday, January 1  
1   Monday, January 21  
2  Monday, February 18  
3       Monday, May 26  
4       Friday, July 4  
5                  NaN  
6                  NaN  
7                  NaN  
8                  NaN  
9                  NaN